In [4]:
import librosa
import os
import numpy as np
import scipy
from scipy.io import wavfile
import scipy.fftpack as fft
from scipy.signal import get_window
import matplotlib.pyplot as plt
from python_speech_features import mfcc
import  torch

ann_folder = '/content/drive/My Drive/SSP/EmoDB/lablaut/'
wav_folder = '/content/drive/My Drive/SSP/EmoDB/wav/'

In [5]:
# Assign data folders

ann_folder = 'lablaut/'
wav_folder = 'wav/'

In [6]:
emotions={'N':"Neutral",'W':"Ärger",'L':"Langeweile",'E':"Ekel",'A':"Angst",'F':"Freude",'T':"Trauer"}
emocoding = list(emotions.keys())
X=[]
y=[]
for filename in os.listdir(wav_folder):
    (Fs,sig) = wavfile.read(wav_folder+filename)
    mfcc_feat = mfcc(sig[:8000],Fs,winfunc=np.hanning,numcep=8)
    mfcc_feat = np.array(mfcc_feat)
    mfcc_feat = mfcc_feat.flatten('C')
    X.append(list(mfcc_feat))
    y.append(emocoding.index(filename[5]))

/home/masterg/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:6: WavFileWarning: Chunk (non-data) not understood, skipping it.
  


In [27]:
# Alternate feature extraction

filename = os.listdir(wav_folder)[0]


n_mfcc_coeffs = 12
n_formant_lpc_coeffs = 12
n_formants = 3

length_of_frame_in_seconds = 20 / 1000
# Hop len is same as frame len for now

X_formant = []
X_energy = []
X_pitch = []

# filename = os.listdir(wav_folder)[2]

for filename in os.listdir(wav_folder):

    path = wav_folder+filename
    x, sr = librosa.load(path)
    frame_len = int(length_of_frame_in_seconds * sr)
    hop_len = frame_len

    # MFCC
    mfccs = librosa.feature.mfcc(x, sr=sr, n_mfcc=n_mfcc_coeffs, n_fft=frame_len, hop_length=hop_len)
    mfccs = mfccs.T

    # Formants
    frames = librosa.util.frame(x, frame_length=frame_len, hop_length=hop_len)
    frames = frames.T

    n_coeff = n_formant_lpc_coeffs

    formants = []

    for frame in frames:
        
        if np.all((frame == 0)):
            formants.append([0.] * n_formants)
            break

        w = np.hamming(len(frame))
        f = (frame * w).astype(np.float64)
        A = librosa.core.lpc(f, n_coeff)

        rts = np.roots(A)
        rts = rts[np.imag(rts) >= 0]
        angz = np.arctan2(np.imag(rts), np.real(rts))
        frqs = angz * (sr / (2 *  np.pi))
        frqs.sort()

        frqs=[i for i in frqs if(i>0.0)]

        if(len(frqs)>=3):
            forms = frqs[0:n_formants]
        else:
            forms = frqs

        assert len(forms) == 3

        formants.append(np.array(forms))
    
    formants = np.array(formants).flatten('C')
    
    # Pitch
    pitches = []

    for frame in frames:
        max_s = int(sr * 1/50)
        min_s = int(sr * 1/500)

        # frame = [i/32767 for i in frame]

        c = librosa.autocorrelate(frame, max_s)

        z = c[round(len(c)/2):]
        z = z[min_s : max_s]
        zmax = max(z)

        index = np.where(z==zmax)
        index = index[0][0]

        pitch = sr/(min_s + index + 2)

        pitches.append(pitch)

    # Energy
    energies = []

    for frame in frames:
        energy = librosa.feature.rms(frame, frame_length=frame_len, hop_length=frame_len)
        energies.append(energy[0, 0])

    X_formant.append(formants)
    X_energy.append(energies)
    X_pitch.append(pitches)


In [30]:
from sklearn.decomposition import PCA
pca = PCA(n_components=2)
pca.fit_transform(X_e)

ValueError: setting an array element with a sequence.

In [28]:
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier

X_train, X_test, y_train, y_test = train_test_split(X_formant, y, test_size=0.33, random_state=42)
clf = MLPClassifier(solver='adam', alpha=1,hidden_layer_sizes=(100,50,25,8), random_state=1, max_iter = 1000)




In [29]:
clf.fit(X_train,y_train)
clf.score(X_test,y_test)

/home/masterg/anaconda3/lib/python3.7/site-packages/numpy/core/_asarray.py:83: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order)


ValueError: Expected 2D array, got 1D array instead:
array=[array([ 217.96682528, 1675.22090946, 3160.44026599, 1613.03208843,
       3326.55348676, 4734.19590538, 1554.32893039, 3271.28719683,
       4508.4892732 , 1375.1249458 , 3192.08533986, 4772.32663155,
       1611.97024244, 3392.85528623, 4960.13853555,  217.90125109,
       1363.60039029, 3245.26379671,  409.59801483, 1366.09395578,
       2970.54771481,  485.5656875 , 1277.83101212, 2921.7661855 ,
        335.30674453, 1329.99265439, 2203.84571451,  218.88284003,
       1803.41330722, 2926.2243065 ,  202.1504657 ,  891.48103428,
       2793.81162169,  285.80676828, 1653.05836831, 2940.89947806,
        358.43374765, 1497.06704078, 2775.04483125,  284.39445768,
       1625.46145874, 2849.65524038,  179.88406741, 1474.48937064,
       2938.19836704,  193.24815147, 1411.50361868, 2810.67514485,
        187.33161304, 1619.23045045, 3076.39237024,  166.17982277,
       2000.1440344 , 3370.76194349,  141.31151153, 2468.52366152,
  

In [7]:
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)
clf = MLPClassifier(solver='adam', alpha=1,hidden_layer_sizes=(100,50,25,8), random_state=1, max_iter = 1000)

clf.fit(X_train,y_train)
clf.score(X_test,y_test)

/home/masterg/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (1000) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


0.3954802259887006

In [ ]:
from sklearn.model_selection import train_test_split

X = []
lengths = []
y = []
emotions={'N':"Neutral",'W':"Ärger",'L':"Langeweile",'E':"Ekel",'A':"Angst",'F':"Freude",'T':"Trauer"}
emocoding = list(emotions.keys())
for filename in os.listdir(wav_folder):
    (Fs,sig) = wavfile.read(wav_folder+filename)
    mfcc_feat = mfcc(sig,Fs,winfunc=np.hanning)
    X.append(torch.tensor(mfcc_feat).float())
    print(mfcc_feat.shape)
    lengths.append(len(mfcc_feat))
    empty = [0]*7
    empty[emocoding.index(filename[5])]=1
    y.append(empty)

(678, 13)
(278, 13)
(143, 13)
(224, 13)
(535, 13)
(390, 13)
(245, 13)
(260, 13)
(339, 13)
(265, 13)
(321, 13)
(533, 13)
(223, 13)
(589, 13)
(215, 13)
(897, 13)
(373, 13)
(379, 13)
(306, 13)
(318, 13)
(308, 13)
(348, 13)
(147, 13)
(216, 13)
(339, 13)
(345, 13)
(317, 13)
(401, 13)
(419, 13)
(297, 13)
(262, 13)
(269, 13)
(155, 13)
(188, 13)
(213, 13)
(335, 13)
(301, 13)
(207, 13)
(405, 13)
(520, 13)
(157, 13)
(168, 13)
(201, 13)
(595, 13)
(173, 13)
(407, 13)
(270, 13)
(246, 13)
(223, 13)
(162, 13)
(299, 13)
(331, 13)
(386, 13)
(221, 13)
(279, 13)
(365, 13)
(163, 13)
(175, 13)
(313, 13)
(334, 13)
(330, 13)
(236, 13)
(147, 13)
(242, 13)
(200, 13)
(284, 13)
(208, 13)
(209, 13)
(220, 13)
(219, 13)
(244, 13)
(212, 13)
(211, 13)
(237, 13)
(149, 13)
(149, 13)
(190, 13)
(178, 13)
(266, 13)
(364, 13)
(161, 13)
(334, 13)
(199, 13)
(270, 13)
(540, 13)
(291, 13)
(242, 13)
(403, 13)
(317, 13)
(318, 13)
(393, 13)
(277, 13)
(279, 13)
(153, 13)
(264, 13)
(391, 13)
(271, 13)
(206, 13)
(261, 13)
(216, 13)


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:9: WavFileWarning: Chunk (non-data) not understood, skipping it.
  if __name__ == '__main__':


(304, 13)
(292, 13)
(304, 13)
(159, 13)
(304, 13)
(233, 13)
(374, 13)
(159, 13)
(294, 13)
(398, 13)
(289, 13)
(343, 13)
(295, 13)
(310, 13)
(271, 13)
(254, 13)
(247, 13)
(251, 13)
(269, 13)
(218, 13)
(200, 13)
(294, 13)
(145, 13)
(353, 13)
(392, 13)
(360, 13)
(309, 13)
(225, 13)
(504, 13)
(234, 13)
(258, 13)
(151, 13)
(343, 13)
(147, 13)
(176, 13)
(150, 13)
(207, 13)
(146, 13)
(165, 13)
(236, 13)
(383, 13)
(212, 13)
(213, 13)
(244, 13)
(296, 13)
(206, 13)
(232, 13)
(621, 13)
(278, 13)
(248, 13)
(348, 13)
(194, 13)
(331, 13)
(180, 13)
(512, 13)
(241, 13)
(406, 13)
(267, 13)
(376, 13)
(264, 13)
(418, 13)
(275, 13)
(179, 13)
(235, 13)
(317, 13)
(221, 13)
(394, 13)
(234, 13)
(203, 13)
(152, 13)
(311, 13)
(153, 13)
(357, 13)
(274, 13)
(331, 13)
(167, 13)
(228, 13)
(382, 13)
(286, 13)
(324, 13)
(147, 13)
(298, 13)
(317, 13)
(228, 13)
(354, 13)
(198, 13)
(276, 13)
(196, 13)
(320, 13)
(239, 13)
(288, 13)
(282, 13)
(310, 13)
(209, 13)
(276, 13)
(235, 13)
(177, 13)
(244, 13)
(363, 13)
(303, 13)


In [ ]:
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence, pack_padded_sequence, pad_packed_sequence

params = {'batch_size': 64,
          'shuffle': True,
          'num_workers': 6}
max_epochs = 100

class MinimalDataset(Dataset):
    def __init__(self, data, labels):
        super().__init__()
        self.data = pad_sequence(data)
        self.labels = torch.tensor(labels)

    def __getitem__(self, index):
        return self.data[index], self.labels[index]

    def __len__(self):
        return len(self.labels)
print(len(X),len(y))
dataset = MinimalDataset(X,y)
data_loader = DataLoader(dataset, **params)
# encoder = GRU(input_size=pad_sequence.data.size,hidden_size=3)

535 535


In [ ]:
print(dataset[0][0].size())
from torch import nn
class Net(nn.Module):

    def __init__(self):
        super(Net, self).__init__()

        self.fc1 = nn.Linear(13,120)
        self.fc2 = nn.Linear(120, 84)
        self.fc3 = nn.Linear(84, len(emocoding))
    
    def forward(self,x):
        x = self.fc1(x)
        x = self.fc2(x)
        x = self.fc3(x)
        return x

net = Net()
print(Net)
import torch.optim as optim

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.001, momentum=0.9)


torch.Size([535, 13])
<class '__main__.Net'>


In [ ]:
from tqdm import tqdm, tqdm_notebook, tnrange
num_batch = len(data_loader)
for epoch in tnrange(max_epochs):
    running_loss=0.0
    t = tqdm_notebook(iter(data_loader), leave=False, total=num_batch)
    for input, label in t:
        optimizer.zero_grad()

        outputs = net(input)
        loss = criterion(outputs, label)
        loss.backward()
        optimizer.step()
        running_loss += loss.item()
    print(running_loss)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: TqdmDeprecationWarning: Please use `tqdm.notebook.trange` instead of `tqdm.tnrange`
  This is separate from the ipykernel package so we can avoid doing imports until


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """


66.89940071105957


54.55457401275635


50.036741733551025


...

47.004939556121826


46.98560810089111


47.12592887878418


46.82814311981201


46.942604064941406



In [ ]:
from sklearn.metrics import accuracy_score, f1_score
# for i in range(100):
#     input = X[i]
#     label = torch.tensor(y[i])
#     output = net(input)
#     print(output.size())
#     print(torch.argmax(label))
#     if(torch.argmax(output)==torch.argmax(label)):
#         accuracy+=1
# print(accuracy)
print(f1_score(output))